In [11]:
from __future__ import print_function

"""
A reference implementation of cavity quantum electrodynamics 
configuration interactions singles.
"""

__authors__   = ["Jon McTague", "Jonathan Foley"]
__credits__   = ["Jon McTague", "Jonathan Foley"]

__copyright_amp__ = "(c) 2014-2018, The Psi4NumPy Developers"
__license__   = "BSD-3-Clause"
__date__      = "2021-01-15"

# ==> Import Psi4, NumPy, & SciPy <==
import psi4
import numpy as np
from helper_cqed_rhf import *
from helper_cis import *
from helper_cs_cqed_cis import *
from psi4.driver.procrouting.response.scf_response import tdscf_excitations
import py3Dmol
# Set Psi4 & NumPy Memory Options
psi4.set_memory('2 GB')
#psi4.core.set_output_file('output.dat', False)

numpy_memory = 2


# Quick validation
In the next cell, we will just run a quick test of helper_cis() and helper_cqed_cis() against psi4's CIS.
Note that helper_cis is just ordinary cis but also returns the dipole expectation value of
excited CIS states, which to my knowledge is not available through psi4.
The function helper_cs_cqed_cis() is the cqed-cis method in the coherent state basis.
If the lambda_vector = 0, then all three of these methods should return the same excited-state energies.

In [12]:
mol_str = """
Mg
H 1 2.1
symmetry c1
1 1
"""

# options dict
options_dict = {'basis': 'sto-3g',
               'save_jk': True, 
               'scf_type': 'pk'}

# set psi4 options and geometry
psi4.set_options(options_dict)
mol = psi4.geometry(mol_str)


# photon energy
om = 7.0 / 27.211

# electric field strength 
E_au = 0.01

# strength for the dipole self energy
l = E_au / np.sqrt(om/2)
lam = np.array([0,0,l])

# run psi4 SCF
psi4_rhf_e, wfn = psi4.energy("scf/sto-3g", return_wfn=True, molecule=mol)
    
# run helper_cs_cqed_cis()
cqed_dict = cs_cqed_cis(lam, mol_str, options_dict, om)

cqed_cis_e = cqed_dict['cqed_cis excitation energies']
scf_e = cqed_dict['rhf_energy']

-197.42866783885827

Start SCF iterations:

Canonical RHF One-electron energy = -279.3208577955504097
CQED-RHF One-electron energy = -279.3212423122716359
Nuclear repulsion energy = 3.0238697752571420
Dipole energy = 0.0041301793270574
SCF Iteration   1: Energy = -197.4257742264784667   dE = -1.97426E+02   dRMS = 1.88864E-04
SCF Iteration   2: Energy = -197.4257832696432615   dE = -9.04316E-06   dRMS = 7.36336E-05
SCF Iteration   3: Energy = -197.4257841305744989   dE = -8.60931E-07   dRMS = 2.15275E-05
SCF Iteration   4: Energy = -197.4257842227148103   dE = -9.21403E-08   dRMS = 7.52653E-06
Performed QED-RHF on the following molecule

Mg
H 1 2.1
symmetry c1
1 1

Total time for SCF iterations: 0.003 seconds 

QED-RHF   energy: -197.42578422 hartree
Psi4  SCF energy: -197.42866784 hartree


In [13]:
ndocc = wfn.nalpha()
nmo = wfn.nmo()
nvirt = nmo-ndocc

print(ndocc)
print(nvirt)
MO = cqed_dict['cqed_rhf_transformation_vectors'] 
MO_occ = MO[:,:ndocc]
MO_virt = MO[:, ndocc:]

CVEC = cqed_dict['cqed_cis eigenvectors']

nto_dict = get_nto(CVEC, MO_occ, MO_virt)
a = np.sum(nto_dict['weights LP0'])
b = np.sum(nto_dict['weights LP1'])
c = np.sum(nto_dict['weights UP0'])
d = np.sum(nto_dict['weights UP1'])
print(a+b+c+d)

print(nto_dict['weights LP0'])
print(nto_dict['weights LP1'])
print(nto_dict['weights UP0'])
print(nto_dict['weights UP1'])

6
4
1.000767037394999
[4.22416654e-01 7.28038676e-05 4.43926302e-05 4.43926302e-05]
[9.05260635e-03 1.05519666e-06 5.06195558e-07 5.06195558e-07]
[5.53404998e-01 9.44611375e-05 5.21511460e-05 5.21511460e-05]
[1.55269166e-02 1.71113845e-06 8.65883562e-07 8.65883562e-07]


In [14]:
# get dictionary form of wavefunction
wfn_dict = psi4.core.Wavefunction.to_file(wfn)
#### uncomment Get orbitals from CQED
wfn_dict['matrix']['Ca'] = nto_dict['NTO UP1']
wfn_dict['matrix']['Cb'] = nto_dict['NTO UP1']
# update wfn object
wfn_cqed_cis = psi4.core.Wavefunction.from_file(wfn_dict) 


In [17]:
psi4.set_options({
    'CUBEPROP_TASKS': ['ORBITALS'],
    'CUBEPROP_ORBITALS': [5,6,7,8],
})
cube = psi4.cubeprop(wfn_cqed_cis)
mol.save_xyz_file("mgh.xyz", 1)
f = open("mgh.xyz")
xyz = f.read()
f.close()


In [20]:
fnto = open("Psi_a_6_6-A.cube")
datanto = fnto.read()
fnto.close()
v = py3Dmol.view()
v.addVolumetricData(datanto, "cube", {'isoval': -0.075, 'color': "red", 'opacity': 0.80})
v.addVolumetricData(datanto, "cube", {'isoval': 0.075, 'color': "blue", 'opacity': 0.80})
v.addModel(xyz, 'mol')
v.setStyle({'stick':{}})
v.zoomTo()
v.show()

You appear to be running in JupyterLab (or JavaScript failed to load for some other reason). You need to install the 3dmol extension: 
 jupyter labextension install jupyterlab_3dmol